In [43]:
%load_ext autoreload
%autoreload 2
%env ANYWIDGET_HMR=1
%load_ext rpy2.ipython

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
env: ANYWIDGET_HMR=1
The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [44]:
from surprise_explora import Widget

w = Widget()

## Create Dataframe

Create a dataframe with fips, group's population, and rates

In [45]:
%%R -o poverty_data
#Install packages
install.packages('tidycensus')

#load packages
library(tidycensus)
library(dplyr)
library(tidyr)
library(stringr)

#Set API Key
Sys.setenv(CENSUS_KEY="f7332e69229418824c5765d1baad389fdb9b923c")

# Target variables
poverty_vars <- c(
  white_total    = "B17001A_001",  # Total White population
  white_poverty  = "B17001A_002",  # White population below poverty
  black_total    = "B17001B_001",  # Total Black population
  black_poverty  = "B17001B_002",  # Black population below poverty
  hispanic_total    = "B17001I_001",  # Total Hispanic population
  hispanic_poverty  = "B17001I_002",   # Hispanic population below poverty
  county_total = "B17001_001", # Total County Population
  county_poverty = "B17001_002" # Total County Poverty
)

# Retrieve county-level data
poverty_data <- get_acs(
  geography = "county",
  variables = poverty_vars,
  year = 2021,
  survey = "acs5",
  output    = "wide"
)


The downloaded binary packages are in
	/var/folders/fr/sw6vgkr93zn67yqw2mnd3dvw0000gr/T//RtmpN9oqp0/downloaded_packages


trying URL 'https://mirror.las.iastate.edu/CRAN/bin/macosx/big-sur-arm64/contrib/4.4/tidycensus_1.7.1.tgz'
Content type 'application/x-gzip' length 3554938 bytes (3.4 MB)
downloaded 3.4 MB

Getting data from the 2017-2021 5-year ACS


In [46]:
import pandas as pd

poverty_data_by_race = poverty_data.copy()

poverty_data_by_race["poverty_rate_white"]   = (poverty_data_by_race["white_povertyE"]   / poverty_data_by_race["white_totalE"])   * 100
poverty_data_by_race["poverty_rate_black"]   = (poverty_data_by_race["black_povertyE"]   / poverty_data_by_race["black_totalE"])   * 100
poverty_data_by_race["poverty_rate_hispanic"] = (poverty_data_by_race["hispanic_povertyE"] / poverty_data_by_race["hispanic_totalE"]) * 100
poverty_data_by_race["poverty_rate_all"]     = (poverty_data_by_race["county_povertyE"]  / poverty_data_by_race["county_totalE"])  * 100

poverty_data_by_race = poverty_data_by_race.rename(columns={
    "white_totalE":    "population_white",
    "black_totalE":    "population_black",
    "hispanic_totalE": "population_hispanic",
    "county_totalE":   "population_all"
})

df = poverty_data_by_race[[
    "GEOID",                    
    "NAME",
    "poverty_rate_black",
    "population_black",
    "poverty_rate_white",
    "population_white",
    "poverty_rate_hispanic",
    "population_hispanic",
    "poverty_rate_all",
    "population_all"
]].rename(columns={"GEOID": "fips"})

df

fips                              NAME  poverty_rate_black  \
1     01001           Autauga County, Alabama           24.573589   
2     01003           Baldwin County, Alabama           20.576692   
3     01005           Barbour County, Alabama           36.152797   
4     01007              Bibb County, Alabama           33.695652   
5     01009            Blount County, Alabama           23.349436   
...     ...                               ...                 ...   
3217  72145  Vega Baja Municipio, Puerto Rico           33.499377   
3218  72147    Vieques Municipio, Puerto Rico           11.764706   
3219  72149   Villalba Municipio, Puerto Rico           54.044944   
3220  72151    Yabucoa Municipio, Puerto Rico           54.194069   
3221  72153      Yauco Municipio, Puerto Rico           55.172414   

      population_black  poverty_rate_white  population_white  \
1              11374.0           10.286056           43418.0   
2              19109.0            7.522396          190099.0   
3              10262.0           14.060850           10419.0   
4               4232.0           12.979423           16426.0   
5                621.0           12.741977           54034.0   
...                ...                 ...               ...   
3217            2409.0           43.903077           30581.0   
3218             629.0           57.098765            2592.0   
3219            1780.0           47.187560           10418.0   
3220           16118.0           53.044570            3186.0   
3221            1276.0           43.812134           24443.0   

      poverty_rate_hispanic  population_hispanic  poverty_rate_all  \
1                 13.597734               1765.0         13.578474   
2                 18.329028              10066.0          9.204905   
3                 60.356789               1009.0         26.471910   
4                 13.764511                603.0         16.942857   
5                 25.808180               5599.0         13.236630   
...                     ...                  ...               ...   
3217              43.179717              53011.0         43.361233   
3218              55.311929               7662.0         53.204280   
3219              44.524789              22127.0         44.494979   
3220              52.686750              31004.0         52.622254   
3221              46.291747              34194.0         46.439216   

      population_all  
1            57790.0  
2           223772.0  
3            22250.0  
4            21000.0  
5            58323.0  
...              ...  
3217         54242.0  
3218          8317.0  
3219         22207.0  
3220         31042.0  
3221         34557.0  

[3221 rows x 10 columns]

In [47]:
df['state'] = df['NAME'].str.split(', ').str[1].str.strip()

df["name"] = df["NAME"].str.split(", ").str[0]

df['white_pop'] = df['population_white']
df['black_pop'] = df['population_black']
df['hispanic_pop'] = df['population_hispanic']
df['global_rate'] = df['poverty_rate_all']
df['global_pop'] = df['population_all']


df['white_rate'] = df['poverty_rate_white']
df['black_rate'] = df['poverty_rate_black']
df['hispanic_rate'] = df['poverty_rate_hispanic']
df = df.drop(columns=['population_white', 'population_black', 'population_hispanic', 'poverty_rate_all', 'population_all', 'poverty_rate_white', 'poverty_rate_black', 'poverty_rate_hispanic'])

In [48]:
df

fips                              NAME        state  \
1     01001           Autauga County, Alabama      Alabama   
2     01003           Baldwin County, Alabama      Alabama   
3     01005           Barbour County, Alabama      Alabama   
4     01007              Bibb County, Alabama      Alabama   
5     01009            Blount County, Alabama      Alabama   
...     ...                               ...          ...   
3217  72145  Vega Baja Municipio, Puerto Rico  Puerto Rico   
3218  72147    Vieques Municipio, Puerto Rico  Puerto Rico   
3219  72149   Villalba Municipio, Puerto Rico  Puerto Rico   
3220  72151    Yabucoa Municipio, Puerto Rico  Puerto Rico   
3221  72153      Yauco Municipio, Puerto Rico  Puerto Rico   

                     name  white_pop  black_pop  hispanic_pop  global_rate  \
1          Autauga County    43418.0    11374.0        1765.0    13.578474   
2          Baldwin County   190099.0    19109.0       10066.0     9.204905   
3          Barbour County    10419.0    10262.0        1009.0    26.471910   
4             Bibb County    16426.0     4232.0         603.0    16.942857   
5           Blount County    54034.0      621.0        5599.0    13.236630   
...                   ...        ...        ...           ...          ...   
3217  Vega Baja Municipio    30581.0     2409.0       53011.0    43.361233   
3218    Vieques Municipio     2592.0      629.0        7662.0    53.204280   
3219   Villalba Municipio    10418.0     1780.0       22127.0    44.494979   
3220    Yabucoa Municipio     3186.0    16118.0       31004.0    52.622254   
3221      Yauco Municipio    24443.0     1276.0       34194.0    46.439216   

      global_pop  white_rate  black_rate  hispanic_rate  
1        57790.0   10.286056   24.573589      13.597734  
2       223772.0    7.522396   20.576692      18.329028  
3        22250.0   14.060850   36.152797      60.356789  
4        21000.0   12.979423   33.695652      13.764511  
5        58323.0   12.741977   23.349436      25.808180  
...          ...         ...         ...            ...  
3217     54242.0   43.903077   33.499377      43.179717  
3218      8317.0   57.098765   11.764706      55.311929  
3219     22207.0   47.187560   54.044944      44.524789  
3220     31042.0   53.044570   54.194069      52.686750  
3221     34557.0   43.812134   55.172414      46.291747  

[3221 rows x 12 columns]

## Setup Suprise

Create surprise object by adding groups we are interested in.

Then calculate surprise for each fo those groups.

In [49]:
from surprise_explora import Surprise

groups = ['white', 'black', 'hispanic']
rate_keys = ['white_rate', 'black_rate', 'hispanic_rate']
population_keys = ['white_pop', 'black_pop', 'hispanic_pop']
global_rate_key = 'global_rate'
global_population_key = 'global_pop'

surprise = Surprise(
    df=df,
    groups=groups, 
    rate_keys=rate_keys,
    population_keys=population_keys,
    global_rate_key=global_rate_key,
    global_population_key=global_population_key
)

# Calculate surprise for each group
surprise.calculate()

In [50]:
# Dataframe with surprise values for each group
surprise.df

fips                              NAME        state  \
1     01001           Autauga County, Alabama      Alabama   
2     01003           Baldwin County, Alabama      Alabama   
3     01005           Barbour County, Alabama      Alabama   
4     01007              Bibb County, Alabama      Alabama   
5     01009            Blount County, Alabama      Alabama   
...     ...                               ...          ...   
3217  72145  Vega Baja Municipio, Puerto Rico  Puerto Rico   
3218  72147    Vieques Municipio, Puerto Rico  Puerto Rico   
3219  72149   Villalba Municipio, Puerto Rico  Puerto Rico   
3220  72151    Yabucoa Municipio, Puerto Rico  Puerto Rico   
3221  72153      Yauco Municipio, Puerto Rico  Puerto Rico   

                     name  white_pop  black_pop  hispanic_pop  global_rate  \
1          Autauga County    43418.0    11374.0        1765.0    13.578474   
2          Baldwin County   190099.0    19109.0       10066.0     9.204905   
3          Barbour County    10419.0    10262.0        1009.0    26.471910   
4             Bibb County    16426.0     4232.0         603.0    16.942857   
5           Blount County    54034.0      621.0        5599.0    13.236630   
...                   ...        ...        ...           ...          ...   
3217  Vega Baja Municipio    30581.0     2409.0       53011.0    43.361233   
3218    Vieques Municipio     2592.0      629.0        7662.0    53.204280   
3219   Villalba Municipio    10418.0     1780.0       22127.0    44.494979   
3220    Yabucoa Municipio     3186.0    16118.0       31004.0    52.622254   
3221      Yauco Municipio    24443.0     1276.0       34194.0    46.439216   

      global_pop  white_rate  black_rate  hispanic_rate  white_zScore  \
1        57790.0   10.286056   24.573589      13.597734     -0.382730   
2       223772.0    7.522396   20.576692      18.329028     -0.769298   
3        22250.0   14.060850   36.152797      60.356789      0.145272   
4        21000.0   12.979423   33.695652      13.764511     -0.005994   
5        58323.0   12.741977   23.349436      25.808180     -0.039206   
...          ...         ...         ...            ...           ...   
3217     54242.0   43.903077   33.499377      43.179717      4.319468   
3218      8317.0   57.098765   11.764706      55.311929      6.165221   
3219     22207.0   47.187560   54.044944      44.524789      4.778887   
3220     31042.0   53.044570   54.194069      52.686750      5.598139   
3221     34557.0   43.812134   55.172414      46.291747      4.306747   

      white_surprise  black_zScore  black_surprise  hispanic_zScore  \
1          -0.006154     -0.135599       -0.002627        -0.514535   
2          -0.025702     -0.315053       -0.007898        -0.228693   
3           0.001146      0.384289        0.007061         2.310423   
4          -0.000059      0.273967        0.003237        -0.504459   
5          -0.000705     -0.190561       -0.000863         0.223162   
...              ...           ...             ...              ...   
3217        0.057192      0.265155        0.002365         1.272667   
3218        0.024066     -0.710697       -0.003238         2.005637   
3219        0.037217      1.187617        0.009082         1.353929   
3220        0.024226      1.194313        0.027304         1.847036   
3221        0.051102      1.238239        0.008021         1.460681   

      hispanic_surprise  global_zScore  global_surprise  
1             -0.003134      -0.203150        -0.003114  
2             -0.003327      -0.760038        -0.022765  
3              0.010614       1.438577         0.013632  
4             -0.001797       0.225238         0.002082  
5              0.002422      -0.246677        -0.003798  
...                 ...            ...              ...  
3217           0.041892       3.589101         0.052341  
3218           0.025255       4.842420         0.027910  
3219           0.028934       3.733461         0.035068  
3220           

In [51]:
chart =  surprise.bar_chart(state='Alabama')

In [52]:
chart

alt.FacetChart(...)

In [53]:
county_list = ['06037'] #Filter unwanted counties by adding to this county list
df_filtered = surprise.df[~surprise.df["fips"].isin(county_list)]
df_filtered

fips                              NAME        state  \
1     01001           Autauga County, Alabama      Alabama   
2     01003           Baldwin County, Alabama      Alabama   
3     01005           Barbour County, Alabama      Alabama   
4     01007              Bibb County, Alabama      Alabama   
5     01009            Blount County, Alabama      Alabama   
...     ...                               ...          ...   
3217  72145  Vega Baja Municipio, Puerto Rico  Puerto Rico   
3218  72147    Vieques Municipio, Puerto Rico  Puerto Rico   
3219  72149   Villalba Municipio, Puerto Rico  Puerto Rico   
3220  72151    Yabucoa Municipio, Puerto Rico  Puerto Rico   
3221  72153      Yauco Municipio, Puerto Rico  Puerto Rico   

                     name  white_pop  black_pop  hispanic_pop  global_rate  \
1          Autauga County    43418.0    11374.0        1765.0    13.578474   
2          Baldwin County   190099.0    19109.0       10066.0     9.204905   
3          Barbour County    10419.0    10262.0        1009.0    26.471910   
4             Bibb County    16426.0     4232.0         603.0    16.942857   
5           Blount County    54034.0      621.0        5599.0    13.236630   
...                   ...        ...        ...           ...          ...   
3217  Vega Baja Municipio    30581.0     2409.0       53011.0    43.361233   
3218    Vieques Municipio     2592.0      629.0        7662.0    53.204280   
3219   Villalba Municipio    10418.0     1780.0       22127.0    44.494979   
3220    Yabucoa Municipio     3186.0    16118.0       31004.0    52.622254   
3221      Yauco Municipio    24443.0     1276.0       34194.0    46.439216   

      global_pop  white_rate  black_rate  hispanic_rate  white_zScore  \
1        57790.0   10.286056   24.573589      13.597734     -0.382730   
2       223772.0    7.522396   20.576692      18.329028     -0.769298   
3        22250.0   14.060850   36.152797      60.356789      0.145272   
4        21000.0   12.979423   33.695652      13.764511     -0.005994   
5        58323.0   12.741977   23.349436      25.808180     -0.039206   
...          ...         ...         ...            ...           ...   
3217     54242.0   43.903077   33.499377      43.179717      4.319468   
3218      8317.0   57.098765   11.764706      55.311929      6.165221   
3219     22207.0   47.187560   54.044944      44.524789      4.778887   
3220     31042.0   53.044570   54.194069      52.686750      5.598139   
3221     34557.0   43.812134   55.172414      46.291747      4.306747   

      white_surprise  black_zScore  black_surprise  hispanic_zScore  \
1          -0.006154     -0.135599       -0.002627        -0.514535   
2          -0.025702     -0.315053       -0.007898        -0.228693   
3           0.001146      0.384289        0.007061         2.310423   
4          -0.000059      0.273967        0.003237        -0.504459   
5          -0.000705     -0.190561       -0.000863         0.223162   
...              ...           ...             ...              ...   
3217        0.057192      0.265155        0.002365         1.272667   
3218        0.024066     -0.710697       -0.003238         2.005637   
3219        0.037217      1.187617        0.009082         1.353929   
3220        0.024226      1.194313        0.027304         1.847036   
3221        0.051102      1.238239        0.008021         1.460681   

      hispanic_surprise  global_zScore  global_surprise  
1             -0.003134      -0.203150        -0.003114  
2             -0.003327      -0.760038        -0.022765  
3              0.010614       1.438577         0.013632  
4             -0.001797       0.225238         0.002082  
5              0.002422      -0.246677        -0.003798  
...                 ...            ...              ...  
3217           0.041892       3.589101         0.052341  
3218           0.025255       4.842420         0.027910  
3219           0.028934       3.733461         0.035068  
3220           

In [55]:
import altair as alt

# GLOBAL

max_surprise = df_filtered['global_surprise'].max()
min_surprise = df_filtered['global_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

alt.Chart(df_filtered).mark_circle(size=60).encode(
    x='global_pop',
    y='global_zScore',
    color=alt.Color('global_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'global_surprise']
).properties(
    width=800,
    height=400
)

alt.Chart(...)

In [56]:
# WHITE

max_surprise = df_filtered['white_surprise'].max()
min_surprise = df_filtered['white_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

alt.Chart(df_filtered).mark_circle(size=60).encode(
    x='white_pop',
    y='white_zScore',
    color=alt.Color('white_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'white_surprise']
).properties(
    width=800,
    height=400
)

alt.Chart(...)

In [57]:
# BLACK

max_surprise = df_filtered['black_surprise'].max()
min_surprise = df_filtered['black_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

alt.Chart(df_filtered).mark_circle(size=60).encode(
    x='black_pop',
    y='black_zScore',
    color=alt.Color('black_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'black_surprise']
).properties(
    width=800,
    height=400
)

alt.Chart(...)

In [59]:
# HISPANIC

max_surprise = df_filtered['hispanic_surprise'].max()
min_surprise = df_filtered['hispanic_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

alt.Chart(df_filtered).mark_circle(size=60).encode(
    x='hispanic_pop',
    y='hispanic_zScore',
    color=alt.Color('hispanic_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'hispanic_surprise']
).properties(
    width=800,
    height=400
)

alt.Chart(...)